In [1]:
import pandas as pd; pd.set_option('display.max_columns', 100)
import numpy as np
import random
import re
import builtin.utils as ut


StatementMeta(, 4090a608-c7c4-42ac-bada-6fd20d7ad8cd, 3, Finished, Available, Finished)

In [2]:

# Mount external lakehouse  "Bronze" into specified local path.
notebookutils.fs.mount("abfss://8c7d2edc-a6a8-4f1a-bef1-c8b14449cfd3@onelake.dfs.fabric.microsoft.com/a1b6b3d0-9bef-4e2a-a731-81e4d801d7a1", "/lakehouse/Bronze")

import pandas as pd
# Load data into pandas DataFrame from notebookutils.fs.getMountPath('/lakehouse/Bronze/Files/Data_Parquet/users_items.parquet')
df = pd.read_parquet(notebookutils.fs.getMountPath('/lakehouse/Bronze/Files/Data_Parquet/users_items.parquet'))
display(df)


StatementMeta(, 4090a608-c7c4-42ac-bada-6fd20d7ad8cd, 4, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, afb3d7b5-d2e2-48f1-8454-628a9b5c924f)

SynapseWidget(Synapse.DataFrame, 5e44200d-9edf-49c8-8bb4-cd77f058eebd)

In [3]:
ut.data_summ(df)

StatementMeta(, 4090a608-c7c4-42ac-bada-6fd20d7ad8cd, 5, Finished, Available, Finished)

Column                  Data_type  No_miss_Qty  %Missing  Missing_Qty
0      user_id            [<class 'str'>]        88310       0.0            0
1  items_count            [<class 'int'>]        88310       0.0            0
2     steam_id            [<class 'str'>]        88310       0.0            0
3     user_url            [<class 'str'>]        88310       0.0            0
4        items  [<class 'numpy.ndarray'>]        88310       0.0            0

In [4]:
# Convertir los numpy.ndarrays a listas regulares
df['items'] = df['items'].apply(lambda x: x.tolist() if isinstance(x, np.ndarray) else x)


StatementMeta(, 4090a608-c7c4-42ac-bada-6fd20d7ad8cd, 6, Finished, Available, Finished)

In [5]:
df = pd.json_normalize(df.to_dict(orient='records'), record_path=['items'], meta=['user_id', 'items_count', 'steam_id', 'user_url'])

StatementMeta(, 4090a608-c7c4-42ac-bada-6fd20d7ad8cd, 7, Finished, Available, Finished)

In [6]:
ut.data_summ(df)

StatementMeta(, 4090a608-c7c4-42ac-bada-6fd20d7ad8cd, 8, Finished, Available, Finished)

Column        Data_type  No_miss_Qty  %Missing  Missing_Qty
0           item_id  [<class 'str'>]      5153209       0.0            0
1         item_name  [<class 'str'>]      5153209       0.0            0
2   playtime_2weeks  [<class 'int'>]      5153209       0.0            0
3  playtime_forever  [<class 'int'>]      5153209       0.0            0
4           user_id  [<class 'str'>]      5153209       0.0            0
5       items_count  [<class 'int'>]      5153209       0.0            0
6          steam_id  [<class 'str'>]      5153209       0.0            0
7          user_url  [<class 'str'>]      5153209       0.0            0

In [7]:
duplicated = df.loc[df.duplicated()]
duplicated

StatementMeta(, 4090a608-c7c4-42ac-bada-6fd20d7ad8cd, 9, Finished, Available, Finished)

item_id                         item_name  playtime_2weeks  \
164294       20             Team Fortress Classic                0   
164295       50         Half-Life: Opposing Force                0   
164296       70                         Half-Life                0   
164297      130             Half-Life: Blue Shift                0   
164298      220                       Half-Life 2                0   
...         ...                               ...              ...   
4898223  213670  South Park™: The Stick of Truth™                0   
4898224  221910               The Stanley Parable                0   
4898225  261030      The Walking Dead: Season Two                0   
4898226  273110     Counter-Strike Nexon: Zombies                0   
4898227     730  Counter-Strike: Global Offensive                0   

         playtime_forever            user_id items_count           steam_id  \
164294                  5             Nikiad         109  76561198084006094   
164295                  0             Nikiad         109  76561198084006094   
164296                  0             Nikiad         109  76561198084006094   
164297                  0             Nikiad         109  76561198084006094   
164298                198             Nikiad         109  76561198084006094   
...                   ...                ...         ...                ...   
4898223               725  76561198080057659          39  76561198080057659   
4898224                53  76561198080057659          39  76561198080057659   
4898225               253  76561198080057659          39  76561198080057659   
4898226                 0  76561198080057659          39  76561198080057659   
4898227                 0  76561198080057659          39  76561198080057659   

                                                  user_url  
164294                 http://steamcommunity.com/id/Nikiad  
164295                 http://steamcommunity.com/id/Nikiad  
164296                 http://steamcommunity.com/id/Nikiad  
164297                 http://steamcommunity.com/id/Nikiad  
164298                 http://steamcommunity.com/id/Nikiad  
...                                                    ...  
4898223  http://steamcommunity.com/profiles/76561198080...  
4898224  http://steamcommunity.com/profiles/76561198080...  
4898225  http://steamcommunity.com/profiles/76561198080...  
4898226  http://steamcommunity.com/profiles/76561198080...  
4898227  http://steamcommunity.com/profiles/76561198080...  

[59104 rows x 8 columns]

In [8]:
df.drop_duplicates(inplace=True)

StatementMeta(, 4090a608-c7c4-42ac-bada-6fd20d7ad8cd, 10, Finished, Available, Finished)

In [9]:
df = df.rename(columns={'item_id':'Item_id', 'item_name':'Item_name', 'playtime_forever':'Playtime_forever', 'user_id': 'User_id', 'items_count': 'Items_count'})
df.drop(columns=['playtime_2weeks', 'steam_id', 'user_url'], inplace=True)

StatementMeta(, 4090a608-c7c4-42ac-bada-6fd20d7ad8cd, 11, Finished, Available, Finished)

In [10]:
df['Item_id'] = df['Item_id'].fillna(0).astype(int)

StatementMeta(, 4090a608-c7c4-42ac-bada-6fd20d7ad8cd, 12, Finished, Available, Finished)

In [11]:
df.head()

StatementMeta(, 4090a608-c7c4-42ac-bada-6fd20d7ad8cd, 13, Finished, Available, Finished)

Item_id                  Item_name  Playtime_forever            User_id  \
0       10             Counter-Strike                 6  76561197970982479   
1       20      Team Fortress Classic                 0  76561197970982479   
2       30              Day of Defeat                 7  76561197970982479   
3       40         Deathmatch Classic                 0  76561197970982479   
4       50  Half-Life: Opposing Force                 0  76561197970982479   

  Items_count  
0         277  
1         277  
2         277  
3         277  
4         277

In [12]:
archivo_parquet = '/lakehouse/default/Files/Cleaned_Data/uitems.parquet'

# Export to a parquet file.
df.to_parquet(archivo_parquet, index=False)

StatementMeta(, 4090a608-c7c4-42ac-bada-6fd20d7ad8cd, 14, Finished, Available, Finished)